In [ ]:
import geopandas as gpd
import pandas as pd
import numpy as np
import shutil
import glob
import os
import subprocess
import tarfile
import shapely.geometry as shpg
import progressbar
import warnings
import zipfile

In [ ]:
def open_zip_shapefile(fpath, pattern=None):
    with zipfile.ZipFile(fpath, "r") as z:
        for f in z.filelist:
            if f.filename.endswith('.shp'):
                if pattern is not None:
                    if pattern not in f.filename:
                        continue
                fname = f.filename
    return gpd.read_file('zip://' + fpath + '/' + fname)

In [ ]:
shp = open_zip_shapefile('glims_download_51898.zip', pattern='polygons')

In [ ]:
shp = shp.loc[shp.subm_id == 730].copy()

In [ ]:
shp.plot();

In [ ]:
len(shp)

In [ ]:
# Compute areas
shp['area'] = shp.to_crs({'proj':'cea'}).area

# Now the interior things

# We group per anlys_id which is the smalles unit of glacier in GLIMS 
# (a single GLIMSID can have several dates and/or contributor, for example)
grouped = shp.groupby('anlys_id')

# We loop over anlys_id
odf = []
odf_rocks = []
for name, group in progressbar.progressbar(grouped):

    # Basic sanity checks
    assert len(group.glac_id.unique()) == 1
    assert len(group.anlys_time.unique()) == 1
    assert len(group.src_date.unique()) == 1
    assert len(group.release_dt.unique()) == 1
    assert len(group.submitters.unique()) == 1
    assert len(group.analysts.unique()) == 1

    # Select the various (1 - more) main rocks
    mains = group.loc[group.line_type == 'glac_bound'].copy()

    # And all rocks
    rocks = group.loc[group.line_type == 'intrnl_rock']

    # We sort areas to avoid misclassifications
    mains = mains.sort_values('area')

    # Now loop over the mains and check which rocks belong
    for i, main in mains.iterrows():

        try:
            # Check where the rocks belong
            isin = rocks.geometry.within(main.geometry)
        except:
            # An error occurred
            # The ids below have been manually checked - that's not many in light of the thousands of entries
            if main.glac_id in ['G282321E08973S', 'G286431E47184S', 'G293140E68314S', 
                                'G294835E68160S', 'G295727E65746S']:
                mains = mains.drop(i)
                isin = []
            elif main.glac_id in ['G286765E46650S']:
                main['geometry'] = main.geometry.buffer(0)[1]
                isin = rocks.geometry.within(main.geometry)
            elif main.glac_id in ['G282313E08974S', 'G286697E46659S', 'G286765E46650S', 
                                  'G292617E67510S', 'G294132E67719S', 'G012723E47107N']:
                rocks = rocks[rocks.is_valid]
                isin = rocks.geometry.within(main.geometry)
            else:
                raise
        exterior = main.geometry.exterior
        interiors = [p.exterior for p in rocks.loc[isin].geometry]
        if len(interiors) > 0:
            mains.loc[i, 'geometry'] = shpg.Polygon(exterior, interiors)
            rocks = rocks[~isin]

    odf.append(mains)
    odf_rocks.append(rocks)

odf = pd.concat(odf)
odf_rocks = pd.concat(odf_rocks)

In [ ]:
odf_rocks.plot();

In [ ]:
len(odf)

In [ ]:
odf.to_file('chile_in_glims.shp')

In [ ]:
chile = open_zip_shapefile('../../../rgi7_data/l0_support_data/Shape_Inventario_de_Glaciares.zip')
# chile = chile.to_crs(shp.crs)

In [ ]:
mp = chile.loc[chile.geom_type == 'MultiPolygon']

In [ ]:
import matplotlib.pyplot as plt

In [ ]:
for i in range(20):
    f, ax = plt.subplots()
    mp.iloc[[i]].plot(ax=ax);
    mp.iloc[[i]].representative_point().plot(ax=ax, color='C3');

In [ ]:
rp = chile.representative_point()
rp = rp.to_frame('geometry')
rp['orig_index'] = chile.index
intersect = gpd.overlay(rp, chile, how='intersection')

In [ ]:
len(intersect), len(chile)

In [ ]:
dupl = intersect.loc[intersect.orig_index.duplicated(keep=False)]

In [ ]:
dupl = chile.loc[dupl.orig_index]

In [ ]:
dupl

In [ ]:
import shapely.geometry as shpg

In [ ]:
chile.geom_type.unique()

In [ ]:
(chile.geom_type == 'MultiPolygon').sum()

In [ ]:
mp = chile.loc[chile.geom_type == 'MultiPolygon']

In [ ]:
mp.iloc[[2]].plot(edgecolor='k')

In [ ]:
ochile = []
for _, s in chile.iterrows():
    if s.geometry.type == 'Polygon':
        ochile.append(s)
    else:
        for g in s.geometry:
            assert g.type == 'Polygon'
            d = s.copy(deep=True)
            d.geometry = g
            ochile.append(s)

In [ ]:
ochile = gpd.GeoDataFrame(ochile)

In [ ]:
ochile.crs = chile.crs

In [ ]:
ochile = ochile.reset_index()

In [ ]:
ochile['index'] = np.arange(len(ochile))

In [ ]:
len(ochile), len(odf)

In [ ]:
ochile['area'] = ochile.to_crs({'proj':'cea'}).area
odf['area'] = odf.to_crs({'proj':'cea'}).area

In [ ]:
ochile['area'].sum() / odf['area'].sum()

In [ ]:
rp = ochile.representative_point()
rp = rp.to_frame('geometry')
rp['orig_index'] = ochile.index
intersect = gpd.overlay(rp, odf, how='intersection')

In [ ]:
found_cl = ochile.loc[intersect.orig_index.values]
len(found)

In [ ]:
found_cl = ochile.loc[intersect['index']]

In [ ]:
found_gl.iloc[[1]].plot();
found_cl.iloc[[1]].plot();

In [ ]:
found_gl.iloc[[2]].plot();
found_cl.iloc[[2]].plot();

In [ ]:
found_gl['area'].sum() / found_cl['area'].sum()

In [ ]:
adif = found_gl['area'].values - found_cl['area']

In [ ]:
adif

In [ ]:
found.iloc[[0]].plot();

In [ ]:
intersect.iloc[[0]].plot();

In [ ]:
intersect

In [ ]:
ochile.iloc[intersect.index]

In [ ]:
ochile.iloc[[0]].plot();maa

In [ ]:
ochile